In [7]:
from hcloud import Client
client = Client(
    token="KccUEiddxtzGoLWSNC3V8tylq7MYHCjdnShtgasQ8jSbHqCjGoaa6Rq7yoz4uS23"
)
PREFIX = "s444498"
YOUR_LOCAL_SSH_PUBKEY = "ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek"
try:
    ssh_key = client.ssh_keys.create(name=f"{PREFIX}-pzc-ssh-key-2", public_key=YOUR_LOCAL_SSH_PUBKEY)
    print(f"Key {ssh_key.data_model.name} created: {ssh_key.data_model.public_key}")
except:
    ssh_key = client.ssh_keys.get_by_name(f"{PREFIX}-pzc-ssh-key-2")
    print(f"Key {ssh_key.data_model.name} already in use: {ssh_key.data_model.public_key}")

Key s444498-pzc-ssh-key-2 already in use: ssh-ed25519 AAAAC3NzaC1lZDI1NTE5AAAAIAj15oTbXA0KGBw5V/76KXDgJZpLNrxUO/rTA0u0eRl1 wirus@wirusowylapek


In [8]:
from hcloud.networks.domain import NetworkSubnet

try:
    vnet = client.networks.create(
        name=f"{PREFIX}-pzc-test-vnet", 
        ip_range="10.10.10.0/24", 
        subnets=[
            NetworkSubnet(ip_range="10.10.10.0/24", network_zone="eu-central", type="cloud")
        ]
    )
    print(f"Created network: {vnet.data_model.name} ({vnet.data_model.ip_range})")
except:
    vnet = client.networks.get_by_name(
        f"{PREFIX}-pzc-test-vnet", 
    )
    print(f"Network in use: {vnet.data_model.name} ({vnet.data_model.ip_range})")

Network in use: s444498-pzc-test-vnet (10.10.10.0/24)


In [9]:
from hcloud.locations.domain import Location
from hcloud.images.domain import Image
from hcloud.server_types.domain import ServerType

cloud_init_vscode=r'''#cloud-config
packages:
  - apt-transport-https
  - ca-certificates
  - curl
  - gnupg-agent
  - software-properties-common
write_files:
  - content: |
        curl -fsSL https://code-server.dev/install.sh > /root/install.sh
        path: /root/install.sh
        owner: root:root
        permissions: '755'
runcmd:
  - bash install.sh
  - code-server --bind-addr 0.0.0.0:8080
  '''

vscode_server = client.servers.create(
    name=f"{PREFIX}-vscode", 
    server_type=ServerType("cx11"), 
    image=Image(name="ubuntu-20.04"), 
    ssh_keys=[ssh_key], 
    networks=[vnet], 
    location=Location("hel1"), 
    user_data=cloud_init_vscode
)

vscode_server.action.wait_until_finished()
print(f"Creating vscode server: {vscode_server.action.complete}")

Creating vscode server: True
